In [1]:
from dash import Dash,html, ctx, dcc, dash_table, Input, Output, State
from dash.dash_table.Format import Format, Scheme
import dash_daq as daq
import plotly.express as px
import pandas as pd

app = Dash(__name__,prevent_initial_callbacks=True)

df=px.data.gapminder()
df

country continent  year  lifeExp       pop   gdpPercap iso_alpha  \
0     Afghanistan      Asia  1952   28.801   8425333  779.445314       AFG   
1     Afghanistan      Asia  1957   30.332   9240934  820.853030       AFG   
2     Afghanistan      Asia  1962   31.997  10267083  853.100710       AFG   
3     Afghanistan      Asia  1967   34.020  11537966  836.197138       AFG   
4     Afghanistan      Asia  1972   36.088  13079460  739.981106       AFG   
...           ...       ...   ...      ...       ...         ...       ...   
1699     Zimbabwe    Africa  1987   62.351   9216418  706.157306       ZWE   
1700     Zimbabwe    Africa  1992   60.377  10704340  693.420786       ZWE   
1701     Zimbabwe    Africa  1997   46.809  11404948  792.449960       ZWE   
1702     Zimbabwe    Africa  2002   39.989  11926563  672.038623       ZWE   
1703     Zimbabwe    Africa  2007   43.487  12311143  469.709298       ZWE   

      iso_num  
0           4  
1           4  
2           4  
3           4  
4           4  
...       ...  
1699      716  
1700      716  
1701      716  
1702      716  
1703      716  

[1704 rows x 8 columns]

In [2]:
app.layout=html.Div([
    html.H2('Callback Example'),
    html.Label('Select a Continent:'),
    dcc.Dropdown(
        df.continent.unique(),
        id = 'select-continent',
    ),
    dcc.Graph(id='continent-graph'),
    dcc.Input(id='message',type='text',value='blah'),
    html.H3('Select Countries to Compare'),
    html.Label('Select First Country:'),
    dcc.Dropdown(id='select-country1'),
    html.Label('Select Second Country:'),
    dcc.Dropdown(id='select-country2'),
    html.Button('Compare',id='compare-button'),
    dcc.Graph(id='country-graph'),
])

@app.callback(
    Output('continent-graph','figure'),
    Output('select-country1','options'),
    Output('select-country2','options'),
    Input('select-continent','value')
)
def continent_selected(continent):
    data = df[df.continent == continent].groupby('year').mean(numeric_only=True).reset_index()
    fig = px.line(data,x='year',y='lifeExp',title=f'Average Life Expectancy in {continent}')
    countries = df[df.continent == continent].country.unique()
    return (fig,countries,countries)

@app.callback(
    Output('country-graph','figure'),
    Input('compare-button','n_clicks'),
    State('select-country1','value'),
    State('select-country2','value')
)
def compare(button,c1,c2):
    subset = df[df.country.isin([c1,c2])]
    return px.line(
        subset,
        x='year',
        y='lifeExp',
        color='country',
        title=f'Life Expectancy for {c1} vs. {c2}'
    )

app.run_server(jupyter_mode='jupyterlab')